In [ ]:
import cv2
import numpy as np
import matplotlib.pyplot as plt


for i in range len(orig_img):
 image = cv2.imread(orig_img[i], cv2.IMREAD_GRAYSCALE)
 equalized_image = cv2.equalizeHist(image)
 fig, axs = plt.subplots(2, 2, figsize=(12, 8))
 image_reshaped = equalized_image.flatten()

 n_clusters = 3  # Number of segments you want
 fuzziness_m = 2  # Fuzziness parameter (usually set to 2)

 cntr, u, _, _, _, _, _ = fuzz.cluster.cmeans(
    data=image_reshaped[np.newaxis, :],  # Data as a 2D array
    c=n_clusters,  
    m=fuzziness_m, 
    error=0.005,  
    maxiter=1000,  
    init=None  
)

 cluster_labels = np.argmax(u, axis=0)

 segmented_image = cluster_labels.reshape(image.shape)

import torch
import cv2
import numpy as np

 model = torch.hub.load('WongKinYiu/yolov7', 'custom', 'yolov7.pt')
 model.eval()

 image_resized = cv2.resize(segmented_image, (640, 640))  # YOLOv7 standard input size
 image_rgb = cv2.cvtColor(image_resized, cv2.COLOR_BGR2RGB)
 image_tensor = torch.from_numpy(image_rgb).float().permute(2, 0, 1) / 255.0
 image_tensor = image_tensor.unsqueeze(0)

 with torch.no_grad():
    detections = model(image_tensor)

# Extracting detection results
 boxes = detections.xyxy[0].cpu().numpy()  # bounding box coordinates
 scores = detections.xywh[0][:, 4].cpu().numpy()  # confidence scores
 classes = detections.xywh[0][:, 5].cpu().numpy()  # class ids

 COCO_CLASSES = [
    'bicycle', 'car', 'motorcycle', 'bus', 'train', 'truck'
]

# Draw bounding boxes on detected cars
 for box, score, class_id in zip(boxes, scores, classes):
    if COCO_CLASSES[int(class_id)] == 'car' || 'bicycle' || 'truck' || 'bus' || 'train' and score > 0.5: 
        x1, y1, x2, y2 = map(int, box[:4])
        label = f"{COCO_CLASSES[int(class_id)]}: {score:.2f}"
        cv2.rectangle(orig_image, (x1, y1), (x2, y2), (0, 255, 0), 2)
        cv2.putText(image, label, (x1, y1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)
        roi = orig_image[y1:y2, x1:x2]
        brisk = cv2.BRISK_create()
        keypoints_brisk, descriptors_brisk= brisk.detectAndCompute(roi, None)
        feature[brisk]=keypoints_brisk
        surf = cv2.xfeatures2d.SURF_create(400)  # Hessian threshold = 400 (can be adjusted)
        surf_keypoints, surf_descriptors = surf.detectAndCompute(roi, None)
        feature[surf]=surf_keypoints
        resnet = models.resnet50(pretrained=True)
        resnet.eval()  # Set to evaluation mode


        transform = transforms.Compose([
         transforms.Resize((224, 224)),
         transforms.ToTensor(),
         transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
    ])

    image_rgb = cv2.cvtColor(roi, cv2.COLOR_BGR2RGB)
    image_pil = transforms.ToPILImage()(image_rgb)
    input_tensor = transform(image_pil).unsqueeze(0)  


    with torch.no_grad():
        features = resnet(input_tensor)
        feature[cnn]=features
import numpy as np
from dbn.tensorflow import SupervisedDBNClassification
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score


X = df.drop(labels = ["Labels"], axis=1)
y = df["Labels"].values 

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

dbn = SupervisedDBNClassification(hidden_layers_structure=[256, 256],  
                                   learning_rate_rbm=0.01,             
                                   learning_rate=0.01,                 
                                   n_epochs_rbm=10,                     
                                   n_iter_backprop=200,                  
                                   batch_size=32,                        
                                   activation_function='sigmoid',     
                                   dropout_p=0.2)                       

dbn.fit(X_train, y_train)

y_pred = dbn.predict(features)

accuracy = accuracy_score(y_test, y_pred)
print(f"Test Accuracy: {accuracy * 100:.2f}%")


#tracking
import cv2
import torch
from yolov5 import YOLOv5
from deep_sort_realtime.deepsort_tracker import DeepSort

# Initialize DeepSORT Tracker
tracker = DeepSort(max_age=30, nn_budget=70, nms_max_overlap=1.0, embedder="mobilenet")

    results = yolo(frame)
    detections = results.xyxy[0].cpu().numpy() 
   
    bboxes = []
    confidences = []
    class_ids = []
    
    for *box, conf, cls in detections:
        if int(cls) == 2:  
            x1, y1, x2, y2 = map(int, box)  
            bboxes.append([x1, y1, x2 - x1, y2 - y1])  
            confidences.append(conf) 
            class_ids.append(int(cls))  
    
    tracks = tracker.update_tracks(bboxes, confidences, frame)
    
    for track in tracks:
        if track.is_confirmed() and track.time_since_update <= 1:
            track_id = track.track_id
            ltrb = track.to_ltrb() 
            x1, y1, x2, y2 = map(int, ltrb)
            cv2.rectangle(frame, (x1, y1), (x2, y2), (0, 255, 0), 2)
            cv2.putText(frame, f"ID: {track_id}", (x1, y1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (255, 0, 0), 2)

    cv2.imshow("Vehicle Tracking", frame)
    if cv2.waitKey(1) & 0xFF == ord('q'):
        break
cap.release()
cv2.destroyAllWindows()


